In [3]:
import os
import pandas as pd
import shutil
df = pd.read_csv('clean_v2.csv', sep=";")

# Danh sách class
class_name = ["HSIL", "LSIL", "NILM", "biến đổi tế bào liên quan đến viêm teo (reactive cellular changes associated with atrophy)", "biến đổi tế bào phản ứng do viêm (reactive cellular changes asociated with inflamation)"]

# Lọc giá trị theo class và tạo thành list mới
filtered_df = df[df['KẾT LUẬN_NEW'].isin(class_name)]

# Thư mục chứa folder ảnh
base_directory = "dataset"

# Nhóm các dòng theo cột "class"
class_grouped = filtered_df.groupby('KẾT LUẬN_NEW')

class_list = {}

for class_name, group in class_grouped:
    # Tạo thư mục cho class nếu chưa tồn tại
    class_folder = os.path.join(base_directory, class_name)
    os.makedirs(class_folder, exist_ok=True)
    
    # Lưu danh sách file vào dictionary
    class_list[class_name] = group["TÊN FILE"].tolist()


    print(class_list)
    
    # Di chuyển từng file vào thư mục tương ứng
    for file_name in class_list[class_name]:
        # Đường dẫn file gốc
        original_file = os.path.join('dataset', file_name)
        
        # Đường dẫn file đích
        destination_file = os.path.join(class_folder, file_name)
        
        # Kiểm tra nếu file tồn tại, thì di chuyển
        if os.path.exists(destination_file) == False:
            shutil.move(original_file, destination_file)
        else:
            print(f"File {file_name} not found!")

# for class_name, filtered_df in class_list.items():
#     print(f"Class: {class_name}: {len(filtered_df)}")


{'HSIL': ['9.png', '10.png', '245.png', '246.png', '2513.png', '2514.png', '4324.png', '4325.png', '5349.png', '5350.png']}
File 9.png not found!
File 10.png not found!
File 245.png not found!
File 246.png not found!
File 2513.png not found!
File 2514.png not found!
File 4324.png not found!
File 4325.png not found!
File 5349.png not found!
File 5350.png not found!
{'HSIL': ['9.png', '10.png', '245.png', '246.png', '2513.png', '2514.png', '4324.png', '4325.png', '5349.png', '5350.png'], 'LSIL': ['35.png', '36.png', '283.png', '284.png']}
File 35.png not found!
File 36.png not found!
File 283.png not found!
File 284.png not found!
{'HSIL': ['9.png', '10.png', '245.png', '246.png', '2513.png', '2514.png', '4324.png', '4325.png', '5349.png', '5350.png'], 'LSIL': ['35.png', '36.png', '283.png', '284.png'], 'NILM': ['5.png', '6.png', '11.png', '12.png', '13.png', '14.png', '17.png', '18.png', '19.png', '20.png', '27.png', '28.png', '29.png', '30.png', '33.png', '34.png', '41.png', '42.png', 

In [4]:

import cv2
import numpy as np
import matplotlib.pyplot as plt


# Định nghĩa kích thước patch
PATCH_SIZE_W = 256  # Giả sử
PATCH_SIZE_H = 256  # Giả sử

# Ngưỡng mật độ
DENSITY_THRESHOLD = 0.25

In [8]:
import os
import cv2
import numpy as np
import matplotlib.pyplot as plt

# Định nghĩa kích thước patch
PATCH_SIZE_W = 256
PATCH_SIZE_H = 256
# Ngưỡng mật độ
DENSITY_THRESHOLD = 0.25

def remove_noise(image):
    # Chuyển đổi sang ảnh xám
    gray = cv2.cvtColor(image, cv2.COLOR_RGB2GRAY)
    # Áp dụng Otsu's thresholding
    _, binary = cv2.threshold(gray, 170, 255, cv2.THRESH_BINARY_INV)
    # Tìm contours
    contours,_ = cv2.findContours(binary, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    # Tạo mask trống
    mask = np.zeros(binary.shape, np.uint8)
    for cnt in contours:
        # Tính diện tích và chu vi
        area = cv2.contourArea(cnt)
        perimeter = cv2.arcLength(cnt, True)
        # Tính độ tròn
        circularity = 4 * np.pi * area / (perimeter * perimeter) if perimeter > 0 else 0
        # Lọc dựa trên kích thước và độ tròn
        if area > 50 and circularity < 0.8:  # Điều chỉnh các giá trị này nếu cần
            cv2.drawContours(mask, [cnt], 0, (255), -1)
    # Áp dụng mask lên ảnh gốc
    result = cv2.bitwise_and(gray, gray, mask=mask)
    return result

def process_image(image_path, output_folder):
    # Load image
    im = cv2.imread(image_path)
    im = cv2.cvtColor(im, cv2.COLOR_BGR2RGB)
    img_h, img_w, _ = im.shape
    w_ratio = int(img_w/PATCH_SIZE_W)
    h_ratio = int(img_h/PATCH_SIZE_H)

    # Lấy tên file gốc không có phần mở rộng
    base_name = os.path.splitext(os.path.basename(image_path))[0]
    
    # Biến đếm để đánh số các phần đã cắt
    patch_counter = 1

    # iterate image upto patch size
    for h in range(h_ratio):
        y_min = h * PATCH_SIZE_H
        y_max = y_min + PATCH_SIZE_H
        for w in range(w_ratio):
            x_min = w * PATCH_SIZE_W
            x_max = x_min + PATCH_SIZE_W
            # Cropping image
            cropped_image = im[y_min:y_max, x_min:x_max]
            # Xử lý nhiễu
            processed_image = remove_noise(cropped_image)
            # Tính mật độ
            foreground = np.sum(processed_image > 0)
            total_pixels = PATCH_SIZE_W * PATCH_SIZE_H
            density = foreground / total_pixels
            if density > DENSITY_THRESHOLD:
                # # Hiển thị ảnh gốc và ảnh đã xử lý
                # fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(10, 5))
                # ax1.imshow(cropped_image)
                # ax1.set_title('Original')
                # ax1.axis('off')
                # ax2.imshow(processed_image, cmap='gray')
                # ax2.set_title(f'Processed (Density: {density:.2f})')
                # ax2.axis('off')
                # plt.show()
                # Save the processed image
                save_path = os.path.join(output_folder, f'{base_name}_{patch_counter}.png')
                cv2.imwrite(save_path, cv2.cvtColor(cropped_image, cv2.COLOR_RGB2BGR))
                patch_counter += 1
            else:
                print(f'Patch at ({h}, {w}) skipped. Density: {density:.2f}')

def process_folders(input_folders):
    for folder in input_folders:
        # Tạo thư mục đầu ra trong thư mục class
        output_folder = os.path.join(folder, 'crop')
        os.makedirs(output_folder, exist_ok=True)
        print("Processing folder", folder)
        for filename in os.listdir(folder):
            if filename.lower().endswith(('.png', '.jpg')):
                image_path = os.path.join(folder, filename)
                print("Processing image path", image_path)
                process_image(image_path, output_folder)

# Danh sách các thư mục đầu vào
input_folders = ['dataset/biến đổi tế bào liên quan đến viêm teo (reactive cellular changes associated with atrophy)',"dataset/biến đổi tế bào phản ứng do viêm (reactive cellular changes asociated with inflamation)", "dataset/HSIL","dataset/LSIL", "dataset/NILM" ]

# Xử lý tất cả các thư mục
process_folders(input_folders)

Processing folder dataset/biến đổi tế bào liên quan đến viêm teo (reactive cellular changes associated with atrophy)
Processing image path dataset/biến đổi tế bào liên quan đến viêm teo (reactive cellular changes associated with atrophy)/1804.png
Patch at (0, 0) skipped. Density: 0.11
Patch at (0, 1) skipped. Density: 0.18
Patch at (0, 2) skipped. Density: 0.10
Patch at (0, 3) skipped. Density: 0.07
Patch at (0, 5) skipped. Density: 0.14
Patch at (0, 6) skipped. Density: 0.16
Patch at (1, 0) skipped. Density: 0.09
Patch at (1, 1) skipped. Density: 0.13
Patch at (1, 4) skipped. Density: 0.15
Patch at (1, 5) skipped. Density: 0.24
Patch at (1, 6) skipped. Density: 0.21
Patch at (2, 0) skipped. Density: 0.02
Patch at (2, 1) skipped. Density: 0.08
Patch at (2, 2) skipped. Density: 0.14
Patch at (2, 3) skipped. Density: 0.16
Patch at (2, 6) skipped. Density: 0.10
Patch at (3, 0) skipped. Density: 0.18
Patch at (3, 1) skipped. Density: 0.12
Patch at (3, 2) skipped. Density: 0.21
Patch at (3,